In [ ]:
# ! git clone https://github.com/iyaja/stylegan-encoder.git
# import os
# os.chdir("stylegan-encoder")

In [18]:
import os
import random
import pickle
import PIL.Image
import numpy as np
import dnnlib
import dnnlib.tflib as tflib
import config
from encoder.generator_model import Generator

import matplotlib.pyplot as plt
%matplotlib inline

In [2]:
URL_FFHQ = 'https://s3-us-west-2.amazonaws.com/nanonets/blogs/karras2019stylegan-ffhq-1024x1024.pkl'

tflib.init_tf()
with dnnlib.util.open_url(URL_FFHQ, cache_dir=config.cache_dir) as f:
    generator_network, discriminator_network, Gs = pickle.load(f)

generator = Generator(Gs, batch_size=1, randomize_noise=False)



Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


In [3]:
def generate_image(latent_vector):
    latent_vector = latent_vector.reshape((1, 18, 512))
    generator.set_dlatents(latent_vector)
    img_array = generator.generate_images()[0]
    img = PIL.Image.fromarray(img_array, 'RGB')
    #return img
    return img.resize((256, 256))

def move_and_show(latent_vector, direction, coeffs):
    fig,ax = plt.subplots(1, len(coeffs), figsize=(15, 10), dpi=80)
    for i, coeff in enumerate(coeffs):
        new_latent_vector = latent_vector.copy()
        new_latent_vector[:8] = (latent_vector + coeff*direction)[:8]
        ax[i].imshow(generate_image(new_latent_vector))
        ax[i].set_title('Coeff: %0.1f' % coeff)
    [x.axis('off') for x in ax]
    plt.show()

In [4]:
# # First, set up the required folders

# os.mkdir('raw_images')
# os.mkdir('aligned_images')
# os.mkdir('generated_images')

In [5]:
# 1) Extract and align faces from images
!python align_images.py raw_images/ aligned_images/

In [6]:
# 2) Find latent representation of aligned image
#    This cell may take a long time (~1 hr)
!python encode_images.py aligned_images/ generated_images/ latent_representations/

/opt/conda/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/opt/conda/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/opt/conda/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:518: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/opt/conda/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:519: FutureWarning: Passing (type, 1) or 

'# Uncomment this semicolon to show output, but be warned it is massive and may crash!'

In [28]:
duration_sec = 5.0
smoothing_sec = 1.0
mp4_fps = 20
num_frames = int(np.rint(duration_sec * mp4_fps))

In [9]:
def generate_image_for_video(latent_vector):
    latent_vector = latent_vector.reshape((1, 18, 512))
    generator.set_dlatents(latent_vector)
    img_array = generator.generate_images()[0]
    
    return img_array
  
def move_for_video(latent_vector, direction, coeff):
    new_latent_vector = latent_vector.copy()
    new_latent_vector[:8] = (latent_vector + coeff*direction)[:8]
  
    img_array = generate_image(new_latent_vector)
  
    return img_array

In [14]:
# Loading already learned representations
a = np.load('latent_representations/a.npy')
b = np.load('latent_representations/b.npy')
c = np.load('latent_representations/c.npy')
d = np.load('latent_representations/d.npy')
e = np.load('latent_representations/e.npy')
f = np.load('latent_representations/f.npy')
g = np.load('latent_representations/g.npy')
h = np.load('latent_representations/h.npy')
i = np.load('latent_representations/i.npy')
j = np.load('latent_representations/j.npy')
k = np.load('latent_representations/k.npy')
l = np.load('latent_representations/l.npy')
m = np.load('latent_representations/m.npy')
n = np.load('latent_representations/n.npy')
o = np.load('latent_representations/o.npy')
p = np.load('latent_representations/p.npy')
q = np.load('latent_representations/q.npy') 

In [15]:
# If you're interpolating between two characters, set these characters here
char1 = a
char2 = b

# This creates an nd array that stores all the image frames fot cross-character interpolation
src_images = np.stack(generate_image_for_video((0.01*alpha*char2)+((1-(0.01*alpha))*char1)) for alpha in range (100))


# Uncomment the next line if you want to do a character transforation video, and choose the arguments as per your requirement
#src_images = np.stack(move_for_video(dany_meme, smile_direction, (0.02*alpha)) for alpha in range (-100,100))


def make_frame(t):
    frame_idx = int(np.clip(np.round(t * mp4_fps), 0, num_frames - 1))
    src_image = src_images[frame_idx]
    return np.array(src_image)

# Generate video.
import moviepy.editor
mp4_file = 'results/interpolate.mp4'
mp4_codec = 'libx264'
mp4_bitrate = '5M'

video_clip = moviepy.editor.VideoClip(make_frame, duration=duration_sec)
video_clip.write_videofile(mp4_file, fps=mp4_fps, codec=mp4_codec, bitrate=mp4_bitrate)

t:  10%|█         | 10/100 [00:00<00:00, 97.94it/s, now=None]

Moviepy - Building video results/interpolate.mp4.
Moviepy - Writing video results/interpolate.mp4



Moviepy - Done !
Moviepy - video ready results/interpolate.mp4


In [32]:
# First Attempts at interpolating between multiple images

mp4_file = 'results/interpolate_random4.mp4'
mp4_codec = 'libx264'
mp4_bitrate = '5M'

images_to_interpolate = [a,c,b]
clips_to_concat = []

from moviepy.editor import VideoFileClip, concatenate_videoclips

def make_frame(t):
    frame_idx = int(np.clip(np.round(t * mp4_fps), 0, num_frames - 1))
    src_image = src_images[frame_idx]
    return np.array(src_image)


# Getting the first image to interpolate from
r = random.randint(0,(len(images_to_interpolate)-1))
prev_image = images_to_interpolate[r]
del images_to_interpolate[r]

i = 0
y = len(images_to_interpolate) - 1

while i < y:
    # pick random latent representation to interpolate to
    k = random.randint(0,(len(images_to_interpolate)-1))
    next_image = images_to_interpolate[k]
    
    src_images = np.stack(generate_image_for_video((0.01*alpha*prev_image)+((1-(0.01*alpha))*next_image)) for alpha in range (100))
    video_clip = moviepy.editor.VideoClip(make_frame, duration=duration_sec)
    clips_to_concat.append(video_clip)
    print(clips_to_concat)
    print(i)
    
    # remove the latent representation used, increment, and continue
    prev_image = next_image
    del images_to_interpolate[k]
    i+=1
    
final_clip = concatenate_videoclips(clips_to_concat)
final_clip.write_videofile(mp4_file, fps=mp4_fps, codec=mp4_codec, bitrate=mp4_bitrate)

KeyboardInterrupt: 